In [1]:
import gym
from gym import spaces
import numpy as np
import random
from src import cube

actionList = [
        'f', 'r', 'l', 'u', 'd', 'b',
        '.f', '.r', '.l', '.u', '.d', '.b']

tileDict = {
    'R' : 0,
    'O' : 1,
    'Y' : 2,
    'G' : 3,
    'B' : 4,
    'W' : 5,
}

class RubiksCubeEnv(gym.Env):
    metadata = {'render.modes': ['human']}

    def __init__(self, orderNum=3):
        # the action is 6 move x 2 direction = 12
        self.action_space = spaces.Discrete(12)
        # input is 9x6 = 54 array
        self.orderNum = orderNum
        low = np.array([0 for i in range(self.orderNum*self.orderNum*6)])
        high = np.array([5 for i in range(self.orderNum*self.orderNum*6)])
        self.observation_space = spaces.Box(low, high, dtype=np.uint8) # flattened
        self.step_count = 0

        self.scramble_low = 1
        self.scramble_high = 10
        self.doScamble = True

    def _seed(self, seed=None):
        self.np_random, seed = seeding.np_random(seed)
        return [seed]

    def step(self, action):
        self.action_log.append(action)
        self.ncube.minimalInterpreter(actionList[action])
        self.state = self.getstate()
        self.step_count = self.step_count + 1

        reward = 0.0
        done = False
        others = {}
        if self.ncube.isSolved() :
            reward = 100.0
            done = True

        if self.step_count > 100 :
            done = True

        return self.state, reward, done, others


    def reset(self):
        self.state = {}
        self.ncube = cube.Cube(order=self.orderNum)
        if self.doScamble:
            self.scramble()
        self.state = self.getstate()
        self.step_count = 0
        self.action_log = []
        return self.state

    def getstate(self):
        return np.array([tileDict[i] for i in self.ncube.constructVectorState()])

    def render(self, mode='human', close=False):
        if close:
            return
        self.ncube.displayCube(isColor=True)

    def setScramble(self, low, high, doScamble=True):
        self.scramble_low = low
        self.scramble_high = high
        self.doScamble = doScamble

    def scramble(self):
        # set the scramber number
        scramble_num = random.randint(self.scramble_low, self.scramble_high)

        # check if scramble
        while self.ncube.isSolved() :
            self.scramble_log = []
            for i in range (scramble_num):
                action = random.randint(0, 11)
                self.scramble_log.append(action)
                self.ncube.minimalInterpreter(actionList[action])

    def getlog(self):
        return self.scramble_log, self.action_log

In [2]:
from stable_baselines3 import SAC, DQN
from stable_baselines3.common.evaluation import evaluate_policy

env = RubiksCubeEnv()

model = DQN("MlpPolicy", env, verbose=1)
model.learn(total_timesteps=int(2e6), progress_bar=True)
model.save("sac_pendulum")

2024-02-16 18:20:25.880425: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-02-16 18:20:26.578836: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /home/liue24/miniconda3/envs/rl-thesis/lib/python3.10/site-packages/cv2/../../lib64:
2024-02-16 18:20:26.579089: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer_plugin.so.7'; dlerror: libnvinfer_plugin.so.7: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /home/liue24/miniconda3/envs/rl-thesis/lib/py

Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/home/liue24/miniconda3/envs/rl-thesis/lib/python3.10/site-packages/stable_baselines3/common/vec_env/patch_gym.py:49: UserWarning: You provided an OpenAI Gym environment. We strongly recommend transitioning to Gymnasium environments. Stable-Baselines3 is automatically wrapping your environments in a compatibility layer, which could potentially cause issues.
  warnings.warn(


Output()

----------------------------------
| rollout/            |          |
|    ep_len_mean      | 101      |
|    ep_rew_mean      | 0        |
|    exploration_rate | 0.998    |
| time/               |          |
|    episodes         | 4        |
|    fps              | 5152     |
|    time_elapsed     | 0        |
|    total_timesteps  | 404      |
----------------------------------


...

----------------------------------
| rollout/            |          |
|    ep_len_mean      | 77.6     |
|    ep_rew_mean      | 24       |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 23684    |
|    fps              | 1093     |
|    time_elapsed     | 1828     |
|    total_timesteps  | 1998677  |
| train/              |          |
|    learning_rate    | 0.0001   |
|    loss             | 0.0052   |
|    n_updates        | 487169   |
----------------------------------


----------------------------------
| rollout/            |          |
|    ep_len_mean      | 77.6     |
|    ep_rew_mean      | 24       |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 23688    |
|    fps              | 1093     |
|    time_elapsed     | 1828     |
|    total_timesteps  | 1998883  |
| train/              |          |
|    learning_rate    | 0.0001   |
|    loss             | 0.147    |
|    n_updates        | 487220   |
----------------------------------


----------------------------------
| rollout/            |          |
|    ep_len_mean      | 76.6     |
|    ep_rew_mean      | 25       |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 23692    |
|    fps              | 1093     |
|    time_elapsed     | 1828     |
|    total_timesteps  | 1999187  |
| train/              |          |
|    learning_rate    | 0.0001   |
|    loss             | 0.0527   |
|    n_updates        | 487296   |
----------------------------------


----------------------------------
| rollout/            |          |
|    ep_len_mean      | 76.6     |
|    ep_rew_mean      | 25       |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 23696    |
|    fps              | 1093     |
|    time_elapsed     | 1829     |
|    total_timesteps  | 1999494  |
| train/              |          |
|    learning_rate    | 0.0001   |
|    loss             | 0.00461  |
|    n_updates        | 487373   |
----------------------------------


----------------------------------
| rollout/            |          |
|    ep_len_mean      | 76.6     |
|    ep_rew_mean      | 25       |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 23700    |
|    fps              | 1093     |
|    time_elapsed     | 1829     |
|    total_timesteps  | 1999803  |
| train/              |          |
|    learning_rate    | 0.0001   |
|    loss             | 0.205    |
|    n_updates        | 487450   |
----------------------------------


In [3]:
# test the model
mean_reward, std_reward = evaluate_policy(model, model.get_env(), n_eval_episodes=1000)
print(f"mean_reward:{mean_reward:.2f} +/- {std_reward:.2f}")

mean_reward:22.10 +/- 41.49
